<a href="https://colab.research.google.com/github/chohyungrae/-study-ing-/blob/master/vibe_demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# VIBE: Video Inference for Human Body Pose and Shape Estimation

Demo of the original PyTorch based implementation provided here: https://github.com/mkocabas/VIBE

## Note
Before running this notebook make sure that your runtime type is 'Python 3 with GPU acceleration'. Go to Edit > Notebook settings > Hardware Accelerator > Select "GPU".

## More Info
- Paper: https://arxiv.org/abs/1912.05656
- Repo: https://github.com/mkocabas/VIBE

In [7]:
# Clone the repo
!git clone https://github.com/mkocabas/VIBE.git

Cloning into 'VIBE'...
remote: Enumerating objects: 14, done.
remote: Counting objects: 100% (14/14), done.
remote: Compressing objects: 100% (14/14), done.
remote: Total 320 (delta 2), reused 0 (delta 0), pack-reused 306
Receiving objects: 100% (320/320), 167.47 KiB | 1.37 MiB/s, done.
Resolving deltas: 100% (135/135), done.


In [8]:
%cd VIBE/

/content/VIBE/VIBE


In [9]:
# Install the other requirements
!pip install torch==1.4.0 numpy==1.17.5
!pip install git+https://github.com/giacaglia/pytube.git --upgrade
!pip install -r requirements.txt

  Cloning https://github.com/giacaglia/pytube.git to /tmp/pip-req-build-r9um1brh
  Running command git clone -q https://github.com/giacaglia/pytube.git /tmp/pip-req-build-r9um1brh
  Created wheel for pytube: filename=pytube-9.5.3-cp36-none-any.whl size=32276 sha256=2b1d8c565e9e4790d54da0c6b30470ba66ce4e4bc981d5f3962377f020ca0a9d
  Stored in directory: /tmp/pip-ephem-wheel-cache-jr9h1u6o/wheels/49/5a/fe/342957c87dc4c1e1a244fbeffcdbf8a0f2c8db0277823f3bfd
Successfully built pytube
  Found existing installation: pytube 9.5.3
    Uninstalling pytube-9.5.3:
      Successfully uninstalled pytube-9.5.3
  Cloning https://github.com/mattloper/chumpy.git to /tmp/pip-req-build-0xzk88wv
  Running command git clone -q https://github.com/mattloper/chumpy.git /tmp/pip-req-build-0xzk88wv
  Cloning https://github.com/mkocabas/yolov3-pytorch.git to /tmp/pip-req-build-qkwzabie
  Running command git clone -q https://github.com/mkocabas/yolov3-pytorch.git /tmp/pip-req-build-qkwzabie
  Cloning https://github

In [10]:
# Download pretrained weights and SMPL data
!source scripts/prepare_data.sh

Downloading...
From: https://drive.google.com/uc?id=1untXhYOLQtpNEy4GTY_0fL_H-k6cTf_r
To: /content/VIBE/VIBE/data/vibe_data.zip
561MB [00:02, 243MB/s]
Archive:  vibe_data.zip
   creating: vibe_data/
  inflating: vibe_data/smpl_mean_params.npz  
  inflating: vibe_data/vibe_model_w_3dpw.pth.tar  
  inflating: vibe_data/gmm_08.pkl    
  inflating: vibe_data/J_regressor_h36m.npy  
  inflating: vibe_data/vibe_model_wo_3dpw.pth.tar  
  inflating: vibe_data/SMPL_NEUTRAL.pkl  
  inflating: vibe_data/J_regressor_extra.npy  
  inflating: vibe_data/spin_model_checkpoint.pth.tar  
  inflating: vibe_data/sample_video.mp4  
  inflating: vibe_data/yolov3.weights  


### Run the demo code.

Check https://github.com/mkocabas/VIBE/blob/master/doc/demo.md for more details about demo.

**Note:** Final rendering is slow compared to inference. We use pyrender with GPU accelaration and it takes 2-3 FPS per image. Please let us know if you know any faster alternative. 

In [11]:
# Run the demo
!python demo.py --vid_file sample_video.mp4 --output_folder output/ --sideview

# You may use --sideview flag to enable from a different viewpoint, note that this doubles rendering time.
# !python demo.py --vid_file sample_video.mp4 --output_folder output/ --sideview

# You may also run VIBE on a YouTube video by providing a link
# python demo.py --vid_file https://www.youtube.com/watch?v=c4DAnQ6DtF8 --output_folder output/ --display

Running "ffmpeg -i sample_video.mp4 -f image2 -v error /tmp/sample_video_mp4/%06d.png"
Images saved to "/tmp/sample_video_mp4"
Input video number of frames 300
Running Multi-Person-Tracker
100% 25/25 [00:18<00:00,  2.91it/s]
Finished. Detection + Tracking FPS 15.60
=> loaded pretrained model from 'data/vibe_data/spin_model_checkpoint.pth.tar'
Performance of pretrained model on 3DPW: 56.56075477600098
Loaded pretrained weights from "data/vibe_data/vibe_model_wo_3dpw.pth.tar"
Running VIBE on each tracklet...
100% 1/1 [00:07<00:00,  7.73s/it]
VIBE FPS: 38.80
Total time spent: 43.33 seconds (including model loading time).
Total FPS (including model loading time): 6.92.
Saving output results to "output/sample_video/vibe_output.pkl".
Rendering output video, writing frames to /tmp/sample_video_mp4_output
100% 300/300 [02:07<00:00,  2.38it/s]
Saving result video to output/sample_video/sample_video_vibe_result.mp4
Running "ffmpeg -y -threads 16 -i /tmp/sample_video_mp4_output/%06d.png -profile:

In [12]:
# Play the generated video
from IPython.display import HTML
from base64 import b64encode

def video(path):
  mp4 = open(path,'rb').read()
  data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
  return HTML('<video width=500 controls loop> <source src="%s" type="video/mp4"></video>' % data_url)

video('output/sample_video/sample_video_vibe_result.mp4')

In [13]:
# Inspect the output file content
import joblib
output = joblib.load('output/sample_video/vibe_output.pkl')
print('Track ids:', output.keys(), end='\n\n')

print('VIBE output file content:', end='\n\n')
for k,v in output[1].items():
  if k != 'joints2d': 
    print(k, v.shape)

Track ids: dict_keys([1])

VIBE output file content:

pred_cam (300, 3)
orig_cam (300, 4)
verts (300, 6890, 3)
pose (300, 72)
betas (300, 10)
joints3d (300, 49, 3)
bboxes (300, 4)
frame_ids (300,)
